In [1]:
import os

import giskard
import mlflow
# src/validate.py
import pandas as pd
from hydra import compose, initialize

from src.data import read_datastore, preprocess_data
from src.model import retrieve_model_with_version

os.chdir("../")

C:\Users\sasha\PycharmProjects\Sum2024MLOps\mlops-11\Lib\site-packages\giskard\core\validation.py:31: RuntimeWarning: fields may not start with an underscore, ignoring "_args"
  validated_func = validate_arguments(func, config={"arbitrary_types_allowed": True})
C:\Users\sasha\PycharmProjects\Sum2024MLOps\mlops-11\Lib\site-packages\giskard\core\validation.py:31: RuntimeWarning: fields may not start with an underscore, ignoring "_kwargs"
  validated_func = validate_arguments(func, config={"arbitrary_types_allowed": True})


In [2]:

# ------------------------------
# 1. Wrap raw dataset
with initialize(config_path="../configs"):
    cfg = compose(config_name="giskard")

version = cfg.test_data_version

df = read_datastore()
print(df.columns)
if 'price' not in df.columns:
    raise ValueError("The 'price' column is missing from the DataFrame.")
# Specify categorical columns and target column
TARGET_COLUMN = cfg.data.target_cols[0]

# CATEGORICAL_COLUMNS = list(cfg.data.cat_cols)

dataset_name = cfg.dataset.name

# Wrap your Pandas DataFrame with giskard.Dataset (validation or test set)
giskard_dataset = giskard.Dataset(
    df=df,  # A pandas.DataFrame containing raw data (before pre-processing) and including ground truth variable.
    target="price",  # Ground truth variable
    name=dataset_name,
)

Index(['property_id', 'location_id', 'page_url', 'property_type', 'price',
       'location', 'city', 'province_name', 'latitude', 'longitude', 'baths',
       'area', 'purpose', 'bedrooms', 'date_added', 'agency', 'agent',
       'Area Type', 'Area Size', 'Area Category'],
      dtype='object')
2024-07-19 03:17:18,255 pid:21532 MainThread giskard.datasets.base INFO     Your 'pandas.DataFrame' is successfully wrapped by Giskard's 'Dataset' wrapper class.
Your 'pandas.DataFrame' is successfully wrapped by Giskard's 'Dataset' wrapper class.


In [3]:

# ------------------------------
# 2. Wrap model
model_name = cfg.model.best_model_name

model_alias = cfg.model.best_model_alias

model_version = cfg.model.best_model_version

print("Model name: ", model_name)
# model: mlflow.pyfunc.PyFuncModel = retrieve_model_with_alias(model_name, model_alias = model_alias)  
model: mlflow.pyfunc.PyFuncModel = retrieve_model_with_version(model_name, model_version)
print("Model loaded successfully")

client = mlflow.MlflowClient()

# mv = client.get_model_version_by_alias(name = model_name, alias=model_alias)
mv = client.get_model_version(name=model_name, version=str(model_version))

model_version = mv.version

Model name:  Lasso


2024/07/19 03:17:19 WARNING mlflow.pyfunc: The version of Python that the model was saved in, `Python 3.10.0`, differs from the version of Python that is currently running, `Python 3.11.0`, and may be incompatible


Model loaded successfully


In [4]:
print("Model input schema: ", model.metadata.get_input_schema())

Model input schema:  ['location_id': double (required), 'latitude': double (required), 'longitude': double (required), 'baths': double (required), 'area': double (required), 'bedrooms': double (required), 'year': double (required), 'property_type_Farm House': double (required), 'property_type_Flat': double (required), 'property_type_House': double (required), 'property_type_Lower Portion': double (required), 'property_type_Penthouse': double (required), 'property_type_Room': double (required), 'property_type_Upper Portion': double (required), 'city_Faisalabad': double (required), 'city_Islamabad': double (required), 'city_Karachi': double (required), 'city_Lahore': double (required), 'city_Rawalpindi': double (required), 'province_name_Islamabad Capital': double (required), 'province_name_Punjab': double (required), 'province_name_Sindh': double (required), 'purpose_For Rent': double (required), 'purpose_For Sale': double (required), 'agency_0': double (required), 'agency_1': double (r

In [5]:
schema = model.metadata.get_input_schema()
print(type(schema))
columns = []
for col in schema:
    column = col.name
    columns.append(column)
print(type(columns[0]))
print(columns)

<class 'mlflow.types.schema.Schema'>
<class 'str'>
['location_id', 'latitude', 'longitude', 'baths', 'area', 'bedrooms', 'year', 'property_type_Farm House', 'property_type_Flat', 'property_type_House', 'property_type_Lower Portion', 'property_type_Penthouse', 'property_type_Room', 'property_type_Upper Portion', 'city_Faisalabad', 'city_Islamabad', 'city_Karachi', 'city_Lahore', 'city_Rawalpindi', 'province_name_Islamabad Capital', 'province_name_Punjab', 'province_name_Sindh', 'purpose_For Rent', 'purpose_For Sale', 'agency_0', 'agency_1', 'agency_2', 'agency_3', 'agency_4', 'agency_5', 'agency_6', 'agency_7', 'agency_8', 'agency_9', 'agency_10', 'agency_11', 'agency_12', 'agency_13', 'agency_14', 'agency_15', 'agency_16', 'agency_17', 'agency_18', 'agency_19', 'agency_20', 'agency_21', 'agency_22', 'agency_23', 'agency_24', 'agency_25', 'agency_26', 'agency_27', 'agency_28', 'agency_29', 'agency_30', 'agency_31', 'agency_32', 'agency_33', 'agency_34', 'agency_35', 'agency_36', 'agency

In [6]:
def transform_data(df):
    print("Original DataFrame columns: ", df.columns)

    X = preprocess_data(
        df=df,
        X_only=True,
    )    
    print("DataFrame after preprocessing: ", X.columns)

    input_schema = columns
    # print("Missing from input schema:")
    for col in X.columns:
        if col not in input_schema:
            X.drop(col, axis=1, inplace=True)
            
    # now fill the missing columns with 0
    # print("Missing from input data:")
    for col in input_schema:
        if col not in X.columns:
            X[col] = float(0)
    # transform all to float
    X = X.astype(float)
    X = pd.DataFrame(X)
    return X

In [7]:
data = transform_data(df[df.columns].head())
data

Original DataFrame columns:  Index(['property_id', 'location_id', 'page_url', 'property_type', 'price',
       'location', 'city', 'province_name', 'latitude', 'longitude', 'baths',
       'area', 'purpose', 'bedrooms', 'date_added', 'agency', 'agent',
       'Area Type', 'Area Size', 'Area Category'],
      dtype='object')
   property_id  location_id  \
0     15829916         1483   
1     15829917         1482   
2     15829919         1482   
3     15829920         1482   
4     15829921         1482   

                                            page_url property_type     price  \
0  https://www.zameen.com/Property/d_h_a_dha_phas...         House  70000000   
1  https://www.zameen.com/Property/d_h_a_dha_phas...         House  75000000   
2  https://www.zameen.com/Property/d_h_a_dha_phas...         House  75000000   
3  https://www.zameen.com/Property/d_h_a_dha_phas...         House  72500000   
4  https://www.zameen.com/Property/d_h_a_dha_phas...         House  80000000   

      

location_id  latitude  longitude     baths  area  bedrooms  year  \
0          1.0       0.0        1.0  0.912871  -2.0  0.912871   0.0   
1          0.0       1.0        0.0  0.000000   0.5  0.000000   0.0   
2          0.0       1.0        0.0 -1.825742   0.5 -1.825742   0.0   
3          0.0       1.0        0.0  0.912871   0.5  0.912871   0.0   
4          0.0       1.0        0.0  0.000000   0.5  0.000000   0.0   

   property_type_House  city_Karachi  province_name_Sindh  ...  \
0                  1.0           1.0                  1.0  ...   
1                  1.0           1.0                  1.0  ...   
2                  1.0           1.0                  1.0  ...   
3                  1.0           1.0                  1.0  ...   
4                  1.0           1.0                  1.0  ...   

   property_type_Penthouse  property_type_Room  property_type_Upper Portion  \
0                      0.0                 0.0                          0.0   
1                      0.0                 0.0                          0.0   
2                      0.0                 0.0                          0.0   
3                      0.0                 0.0                          0.0   
4                      0.0                 0.0                          0.0   

   city_Faisalabad  city_Islamabad  city_Lahore  city_Rawalpindi  \
0              0.0             0.0          0.0              0.0   
1              0.0             0.0          0.0              0.0   
2              0.0             0.0          0.0              0.0   
3              0.0             0.0          0.0              0.0   
4              0.0             0.0          0.0              0.0   

   province_name_Islamabad Capital  province_name_Punjab  purpose_For Rent  
0                              0.0                   0.0               0.0  
1                              0.0                   0.0               0.0  
2                              0.0                   0.0               0.0  
3                              0.0                   0.0               0.0  
4                              0.0                   0.0               0.0  

[5 rows x 1528 columns]

In [8]:
data2 = preprocess_data(df[df.columns].head())
data2

   property_id  location_id  \
0     15829916         1483   
1     15829917         1482   
2     15829919         1482   
3     15829920         1482   
4     15829921         1482   

                                            page_url property_type     price  \
0  https://www.zameen.com/Property/d_h_a_dha_phas...         House  70000000   
1  https://www.zameen.com/Property/d_h_a_dha_phas...         House  75000000   
2  https://www.zameen.com/Property/d_h_a_dha_phas...         House  75000000   
3  https://www.zameen.com/Property/d_h_a_dha_phas...         House  72500000   
4  https://www.zameen.com/Property/d_h_a_dha_phas...         House  80000000   

      location     city province_name   latitude  longitude  baths  \
0  DHA Defence  Karachi         Sindh  24.805045  67.064323      6   
1  DHA Defence  Karachi         Sindh  24.810265  67.043552      5   
2  DHA Defence  Karachi         Sindh  24.810265  67.043552      3   
3  DHA Defence  Karachi         Sindh  24.810265  67

(   location_id  latitude  longitude     baths  area  bedrooms  year  \
 0          1.0       0.0        1.0  0.912871  -2.0  0.912871   0.0   
 1          0.0       1.0        0.0  0.000000   0.5  0.000000   0.0   
 2          0.0       1.0        0.0 -1.825742   0.5 -1.825742   0.0   
 3          0.0       1.0        0.0  0.912871   0.5  0.912871   0.0   
 4          0.0       1.0        0.0  0.000000   0.5  0.000000   0.0   
 
    property_type_House  city_Karachi  province_name_Sindh  ...  city_2  \
 0                  1.0           1.0                  1.0  ...       0   
 1                  1.0           1.0                  1.0  ...       0   
 2                  1.0           1.0                  1.0  ...       0   
 3                  1.0           1.0                  1.0  ...       0   
 4                  1.0           1.0                  1.0  ...       0   
 
    city_3  city_4  province_name_1  province_name_2  purpose_1   day_sin  \
 0       0       0                0  

In [9]:

# ------------------------------
# Initial prediction

def predict(raw_df):
    X = transform_data(
                df=raw_df
                )
    return model.predict(X)


predictions = predict(df[df.columns].head())
print(f"Predictions: {predictions}")

Original DataFrame columns:  Index(['property_id', 'location_id', 'page_url', 'property_type', 'price',
       'location', 'city', 'province_name', 'latitude', 'longitude', 'baths',
       'area', 'purpose', 'bedrooms', 'date_added', 'agency', 'agent',
       'Area Type', 'Area Size', 'Area Category'],
      dtype='object')
   property_id  location_id  \
0     15829916         1483   
1     15829917         1482   
2     15829919         1482   
3     15829920         1482   
4     15829921         1482   

                                            page_url property_type     price  \
0  https://www.zameen.com/Property/d_h_a_dha_phas...         House  70000000   
1  https://www.zameen.com/Property/d_h_a_dha_phas...         House  75000000   
2  https://www.zameen.com/Property/d_h_a_dha_phas...         House  75000000   
3  https://www.zameen.com/Property/d_h_a_dha_phas...         House  72500000   
4  https://www.zameen.com/Property/d_h_a_dha_phas...         House  80000000   

      

In [10]:
X, y = df.drop('price', axis=1), df['price']

In [11]:
# ------------------------------
# 4. Create Giskard model
giskard_model = giskard.Model(
    model=predict,
    model_type="regression",
    feature_names=X.columns,
    name=model_name,
)


2024-07-19 03:17:21,233 pid:21532 MainThread giskard.models.automodel INFO     Your 'prediction_function' is successfully wrapped by Giskard's 'PredictionFunctionModel' wrapper class.
Your 'prediction_function' is successfully wrapped by Giskard's 'PredictionFunctionModel' wrapper class.


In [12]:
print(giskard_model.feature_names)
print(giskard_dataset.df.columns)

['property_id', 'location_id', 'page_url', 'property_type', 'location', 'city', 'province_name', 'latitude', 'longitude', 'baths', 'area', 'purpose', 'bedrooms', 'date_added', 'agency', 'agent', 'Area Type', 'Area Size', 'Area Category']
Index(['property_id', 'location_id', 'page_url', 'property_type', 'price',
       'location', 'city', 'province_name', 'latitude', 'longitude', 'baths',
       'area', 'purpose', 'bedrooms', 'date_added', 'agency', 'agent',
       'Area Type', 'Area Size', 'Area Category'],
      dtype='object')


In [13]:
# ------------------------------
# 3. Scanning model
from sklearn.metrics import r2_score

In [14]:
wrapped_predict = giskard_model.predict(giskard_dataset)
wrapped_test_metric = r2_score(y, wrapped_predict.prediction)

print(f'Wrapped Test R2-score: {wrapped_test_metric:.2f}')

2024-07-19 03:17:21,498 pid:21532 MainThread giskard.datasets.base INFO     Casting dataframe columns from {'property_id': 'int64', 'location_id': 'int64', 'page_url': 'object', 'property_type': 'object', 'location': 'object', 'city': 'object', 'province_name': 'object', 'latitude': 'float64', 'longitude': 'float64', 'baths': 'int64', 'area': 'object', 'purpose': 'object', 'bedrooms': 'int64', 'date_added': 'object', 'agency': 'object', 'agent': 'object', 'Area Type': 'object', 'Area Size': 'float64', 'Area Category': 'object'} to {'property_id': 'int64', 'location_id': 'int64', 'page_url': 'object', 'property_type': 'object', 'location': 'object', 'city': 'object', 'province_name': 'object', 'latitude': 'float64', 'longitude': 'float64', 'baths': 'int64', 'area': 'object', 'purpose': 'object', 'bedrooms': 'int64', 'date_added': 'object', 'agency': 'object', 'agent': 'object', 'Area Type': 'object', 'Area Size': 'float64', 'Area Category': 'object'}
Casting dataframe columns from {'pro

In [15]:
scan_results = giskard.scan(giskard_model, giskard_dataset)
scan_results_path = f"reports/validation_results_{model_name}_{model_version}_{dataset_name}_{version}.html"
scan_results.to_html(scan_results_path)

2024-07-19 03:18:13,337 pid:21532 MainThread giskard.datasets.base INFO     Casting dataframe columns from {'property_id': 'int64', 'location_id': 'int64', 'page_url': 'object', 'property_type': 'object', 'location': 'object', 'city': 'object', 'province_name': 'object', 'latitude': 'float64', 'longitude': 'float64', 'baths': 'int64', 'area': 'object', 'purpose': 'object', 'bedrooms': 'int64', 'date_added': 'object', 'agency': 'object', 'agent': 'object', 'Area Type': 'object', 'Area Size': 'float64', 'Area Category': 'object'} to {'property_id': 'int64', 'location_id': 'int64', 'page_url': 'object', 'property_type': 'object', 'location': 'object', 'city': 'object', 'province_name': 'object', 'latitude': 'float64', 'longitude': 'float64', 'baths': 'int64', 'area': 'object', 'purpose': 'object', 'bedrooms': 'int64', 'date_added': 'object', 'agency': 'object', 'agent': 'object', 'Area Type': 'object', 'Area Size': 'float64', 'Area Category': 'object'}
Casting dataframe columns from {'pro

In [16]:
# show report
display(scan_results)

<iframe id="scan-2365742580752" srcdoc="<!doctype html>
<html lang="en">

<head>
 <title>Giskard Scan Results</title>
 <base target="_blank">
 <meta charset="utf-8">
 
<style>pre code.hljs{display:block;overflow-x:auto;padding:1em}code.hljs{padding:3px 5px}
/*!
 Theme: GitHub Dark
 Description: Dark theme as seen on github.com
 Author: github.com
 Maintainer: @Hirse
 Updated: 2021-05-15

 Outdated base version: https://github.com/primer/github-syntax-dark
 Current colors taken from GitHub's CSS
*/.hljs{background:#0d1117;color:#c9d1d9}.hljs-doctag,.hljs-keyword,.hljs-meta .hljs-keyword,.hljs-template-tag,.hljs-template-variable,.hljs-type,.hljs-variable.language_{color:#ff7b72}.hljs-title,.hljs-title.class_,.hljs-title.class_.inherited__,.hljs-title.function_{color:#d2a8ff}.hljs-attr,.hljs-attribute,.hljs-literal,.hljs-meta,.hljs-number,.hljs-operator,.hljs-selector-attr,.hljs-selector-class,.hljs-selector-id,.hljs-variable{color:#79c0ff}.hljs-meta .hljs-string,.hljs-regexp,.hljs-string{color:#a5d6ff}.hljs-built_in,.hljs-symbol{color:#ffa657}.hljs-code,.hljs-comment,.hljs-formula{color:#8b949e}.hljs-name,.hljs-quote,.hljs-selector-pseudo,.hljs-selector-tag{color:#7ee787}.hljs-subst{color:#c9d1d9}.hljs-section{color:#1f6feb;font-weight:700}.hljs-bullet{color:#f2cc60}.hljs-emphasis{color:#c9d1d9;font-style:italic}.hljs-strong{color:#c9d1d9;font-weight:700}.hljs-addition{background-color:#033a16;color:#aff5b4}.hljs-deletion{background-color:#67060c;color:#ffdcd7}.hljs-copy-wrapper{overflow:hidden;position:relative}.hljs-copy-button:focus,.hljs-copy-wrapper:hover .hljs-copy-button{transform:translateX(0)}.hljs-copy-button{background-color:#2d2b57;background-color:var(--hljs-theme-background);background-image:url('data:image/svg+xml;charset=utf-8,<svg xmlns="http://www.w3.org/2000/svg" width="16" height="16" fill="none" viewBox="0 0 24 24"><path fill="%23fff" fill-rule="evenodd" d="M6 5a1 1 0 0 0-1 1v14a1 1 0 0 0 1 1h12a1 1 0 0 0 1-1V6a1 1 0 0 0-1-1h-2a1 1 0 1 1 0-2h2a3 3 0 0 1 3 3v14a3 3 0 0 1-3 3H6a3 3 0 0 1-3-3V6a3 3 0 0 1 3-3h2a1 1 0 0 1 0 2H6Z" clip-rule="evenodd"/><path fill="%23fff" fill-rule="evenodd" d="M7 3a2 2 0 0 1 2-2h6a2 2 0 0 1 2 2v2a2 2 0 0 1-2 2H9a2 2 0 0 1-2-2V3Zm8 0H9v2h6V3Z" clip-rule="evenodd"/></svg>');background-position:50%;background-repeat:no-repeat;border:1px solid #ffffff22;border-radius:.25rem;color:#fff;height:2rem;position:absolute;right:1em;text-indent:-9999px;top:1em;transition:background-color .2s ease,transform .2s ease-out;width:2rem}.hljs-copy-button:hover{border-color:#ffffff44}.hljs-copy-button:active{border-color:#ffffff66}.hljs-copy-button[data-copied=true]{background-image:none;text-indent:0;width:auto}@media (prefers-reduced-motion){.hljs-copy-button{transition:none}}.hljs-copy-alert{clip:rect(0 0 0 0);-webkit-clip-path:inset(50%);clip-path:inset(50%);height:1px;overflow:hidden;position:absolute;white-space:nowrap;width:1px}
/*! tailwindcss v3.3.2 | MIT License | https://tailwindcss.com*/*,:after,:before{border:0 solid #e5e7eb;box-sizing:border-box}:after,:before{--tw-content:""}html{-webkit-text-size-adjust:100%;font-feature-settings:normal;font-family:ui-sans-serif,system-ui,-apple-system,BlinkMacSystemFont,Segoe UI,Roboto,Helvetica Neue,Arial,Noto Sans,sans-serif,Apple Color Emoji,Segoe UI Emoji,Segoe UI Symbol,Noto Color Emoji;font-variation-settings:normal;line-height:1.5;-moz-tab-size:4;-o-tab-size:4;tab-size:4}body{line-height:inherit;margin:0}hr{border-top-width:1px;color:inherit;height:0}abbr:where([title]){-webkit-text-decoration:underline dotted;text-decoration:underline dotted}h1,h2,h3,h4,h5,h6{font-size:inherit;font-weight:inherit}a{color:inherit;text-decoration:inherit}b,strong{font-weight:bolder}code,kbd,pre,samp{font-family:ui-monospace,SFMono-Regular,Menlo,Monaco,Consolas,Liberation Mono,Courier New,monospace;font-size:1em}small{font-size:80%}sub,sup{font-size:75%;line-height:0;position:relative;vertical-align:baseline}sub{bottom:-.25em}sup{top:-.5em}table{border-collapse:

In [17]:
# 4. Create a test suite
suite_name = f"test_suite_{model_name}_{model_version}_{dataset_name}_{version}"
test_suite = giskard.Suite(name = suite_name)

In [ ]:
# TODO: create a custom giskard function with MAPE

from sklearn.metrics import mean_absolute_percentage_error
from giskard import demo, test, Dataset, TestResult, testing



In [18]:
test1 = giskard.testing.test_rmse(model=giskard_model,
                                 dataset=giskard_dataset,
                                 threshold=1.0)

test_suite.add_test(test1)

In [19]:
test_results = test_suite.run()
if (test_results.passed):
  print("Passed model validation!")
else:
  print("Model has vulnerabilities!")

2024-07-19 03:46:47,219 pid:21532 MainThread giskard.datasets.base INFO     Casting dataframe columns from {'property_id': 'int64', 'location_id': 'int64', 'page_url': 'object', 'property_type': 'object', 'location': 'object', 'city': 'object', 'province_name': 'object', 'latitude': 'float64', 'longitude': 'float64', 'baths': 'int64', 'area': 'object', 'purpose': 'object', 'bedrooms': 'int64', 'date_added': 'object', 'agency': 'object', 'agent': 'object', 'Area Type': 'object', 'Area Size': 'float64', 'Area Category': 'object'} to {'property_id': 'int64', 'location_id': 'int64', 'page_url': 'object', 'property_type': 'object', 'location': 'object', 'city': 'object', 'province_name': 'object', 'latitude': 'float64', 'longitude': 'float64', 'baths': 'int64', 'area': 'object', 'purpose': 'object', 'bedrooms': 'int64', 'date_added': 'object', 'agency': 'object', 'agent': 'object', 'Area Type': 'object', 'Area Size': 'float64', 'Area Category': 'object'}
Casting dataframe columns from {'pro